In [7]:
import torch
import os
from pprint import pprint
import math
import sys
import training as T
from pathlib import Path
sys.path.append(os.getcwd())
sys.path.append(str(Path(os.getcwd()).parent))

In [8]:
seed = sys.argv[1]
dataset = sys.argv[2]

In [9]:
seed = 0
ds_idx = 0

In [12]:
datasets = os.listdir('../ts_datasets/')
datasets = [dataset for dataset in datasets if dataset.endswith('.tsds')]
dataset = datasets[ds_idx]
package = torch.load(f'../ts_datasets/{dataset}')

name = package['name']

N_train = package['N_train']
N_valid = package['N_valid']
N_test = package['N_test']

N_class = package['N_class']

N_channel = package['N_channel']
N_length = package['N_length']

N_feature = N_channel * N_length

print(f'dataset: {name}, N_train: {N_train}, N_valid: {N_valid}, N_test: {N_test}, N_class: {N_class}, N_feature: {N_feature}, N_channel: {N_channel}, N_length: {N_length}')

X_train = package['X_train'].flatten(start_dim=1, end_dim=2)
X_valid = package['X_valid'].flatten(start_dim=1, end_dim=2)
X_test = package['X_test'].flatten(start_dim=1, end_dim=2)

y_train = package['Y_train']
y_valid = package['Y_valid']
y_test = package['Y_test']

print(f'X_train: {X_train.shape}, X_valid: {X_valid.shape}, X_test: {X_test.shape}')

dataset: ProximalPhalanxTW, N_train: 267, N_valid: 133, N_test: 205, N_class: 6, N_feature: 80, N_channel: 1, N_length: 80
X_train: torch.Size([267, 80]), X_valid: torch.Size([133, 80]), X_test: torch.Size([205, 80])


In [13]:
package.keys()

dict_keys(['name', 'X_train', 'Y_train', 'X_valid', 'Y_valid', 'X_test', 'Y_test', 'N_train', 'N_valid', 'N_test', 'N_channel', 'N_length', 'N_class'])

In [14]:
torch.manual_seed(seed)

model = torch.nn.Sequential(torch.nn.Linear(N_feature, 3),
                            torch.nn.Tanh(),
                            torch.nn.Linear(3, N_class),
                            torch.nn.Tanh(),
                             torch.nn.Softmax(dim=1))
pprint(model)

Sequential(
  (0): Linear(in_features=80, out_features=3, bias=True)
  (1): Tanh()
  (2): Linear(in_features=3, out_features=6, bias=True)
  (3): Tanh()
  (4): Softmax(dim=1)
)


In [15]:
loss_fn = torch.nn.CrossEntropyLoss()
optimizer = torch.optim.Adam(model.parameters(), lr=1e-4)

In [16]:
setup = f'{name}_{seed}.mlp'

In [17]:
best_nn = T.training(model, loss_fn, optimizer, X_train, y_train, X_valid, y_valid, X_test, y_test)

epoch:        0 | train loss: 1.79659e+00 | valid loss: 1.79808e+00 | train acc: 0.1536 | valid acc: 0.1278 | test acc: 0.1951 | patience: 0
epoch:        1 | train loss: 1.79647e+00 | valid loss: 1.79795e+00 | train acc: 0.1536 | valid acc: 0.1278 | test acc: 0.1951 | patience: 0
epoch:        2 | train loss: 1.79634e+00 | valid loss: 1.79783e+00 | train acc: 0.1536 | valid acc: 0.1278 | test acc: 0.1951 | patience: 0
epoch:        3 | train loss: 1.79622e+00 | valid loss: 1.79771e+00 | train acc: 0.1536 | valid acc: 0.1278 | test acc: 0.1951 | patience: 0
epoch:        4 | train loss: 1.79610e+00 | valid loss: 1.79758e+00 | train acc: 0.1536 | valid acc: 0.1278 | test acc: 0.1951 | patience: 0
epoch:        5 | train loss: 1.79598e+00 | valid loss: 1.79746e+00 | train acc: 0.1536 | valid acc: 0.1278 | test acc: 0.1951 | patience: 0
epoch:        6 | train loss: 1.79586e+00 | valid loss: 1.79734e+00 | train acc: 0.1536 | valid acc: 0.1278 | test acc: 0.1951 | patience: 0
epoch:       

In [18]:
acc_train = (best_nn(X_train).argmax(dim=1) == y_train).float().mean()
acc_valid = (best_nn(X_valid).argmax(dim=1) == y_valid).float().mean()
acc_test = (best_nn(X_test).argmax(dim=1) == y_test).float().mean()

package = {'name': name, model: best_nn, 'acc_train': acc_train, 'acc_valid': acc_valid, 'acc_test': acc_test}
print(package)

if not os.path.exists('./baseline_result/'):
    os.makedirs('./baseline_result/')
torch.save(package, f'./baseline_result/{setup}')


{'name': 'ProximalPhalanxTW', Sequential(
  (0): Linear(in_features=80, out_features=3, bias=True)
  (1): Tanh()
  (2): Linear(in_features=3, out_features=6, bias=True)
  (3): Tanh()
  (4): Softmax(dim=1)
): Sequential(
  (0): Linear(in_features=80, out_features=3, bias=True)
  (1): Tanh()
  (2): Linear(in_features=3, out_features=6, bias=True)
  (3): Tanh()
  (4): Softmax(dim=1)
), 'acc_train': tensor(0.7116), 'acc_valid': tensor(0.7444), 'acc_test': tensor(0.6780)}
